In [1]:
!pip install resnest

In [2]:
import logging
logging.getLogger().setLevel(logging.CRITICAL)
!pip install pylabel > /dev/null

from pylabel import importer

import os 
import zipfile


In [3]:
from torch.utils.data import Dataset, DataLoader, SubsetRandomSampler
import torch.optim as optim
import gc
from tqdm import tqdm 
import os 
import zipfile
import glob
import pandas as pd
import numpy as np
import pandas as pd
from PIL import Image
import torch
from torchvision import transforms
from PIL import ImageFile
ImageFile.LOAD_TRUNCATED_IMAGES = True
from resnest.torch import resnest200


In [4]:
import sys
import wandb
sys.path.append('/kaggle/usr/lib/wandblogin/')
from wandblogin import login
login()

# # Initialize wandb
wandb.init(project="fracatlas-fracture-bbox-labels-effnet-k-fold")


wandb: WARNING If you're specifying your api key in code, ensure this code is not shared publicly.
wandb: WARNING Consider setting the WANDB_API_KEY environment variable, or running `wandb login` from the command line.
wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc
wandb: Currently logged in as: shyamdgupta (shyam-d-gupta). Use `wandb login --relogin` to force relogin
wandb: wandb version 0.17.1 is available!  To upgrade, please run:
wandb:  $ pip install wandb --upgrade
wandb: Tracking run with wandb version 0.17.0
wandb: Run data is saved locally in /kaggle/working/wandb/run-20240613_124939-lnzvqbpk
wandb: Run `wandb offline` to turn off syncing.
wandb: Syncing run fearless-lion-10
wandb: ⭐️ View project at https://wandb.ai/shyam-d-gupta/fracatlas-fracture-bbox-labels-effnet-k-fold
wandb: 🚀 View run at https://wandb.ai/shyam-d-gupta/fracatlas-fracture-bbox-labels-effnet-k-fold/runs/lnzvqbpk


In [5]:

#Specify path to the coco.json file
path_to_annotations = "/kaggle/input/fracatlas-original-dataset/FracAtlas/Annotations/COCO JSON/COCO_fracture_masks.json"
#Specify the path to the images (if they are in a different folder than the annotations)
path_to_images = "/kaggle/input/fracatlas-original-dataset/FracAtlas/images/Fractured"

#Import the dataset into the pylable schema 
dataset = importer.ImportCoco(path_to_annotations, path_to_images=path_to_images, name="BCCD_coco")
dataset.df.head(5)


img_folder    img_filename  \
id                                                                      
0   /kaggle/input/fracatlas-original-dataset/FracA...  IMG0000019.jpg   
1   /kaggle/input/fracatlas-original-dataset/FracA...  IMG0000025.jpg   
2   /kaggle/input/fracatlas-original-dataset/FracA...  IMG0000044.jpg   
3   /kaggle/input/fracatlas-original-dataset/FracA...  IMG0000057.jpg   
4   /kaggle/input/fracatlas-original-dataset/FracA...  IMG0000058.jpg   

   img_path  img_id  img_width  img_height img_depth ann_segmented  \
id                                                                   
0                 1       2304        2880                           
1                 2       2880        2304                           
2                 3       2304        2880                           
3                 4       2304        2880                           
4                 5       2304        2880                           

    ann_bbox_xmin  ann_bbox_ymin  ...  ann_iscrowd  ann_keypoints  ann_pose  \
id                                ...                                         
0     1242.297030     929.108911  ...            0                            
1     1466.504519    2010.557108  ...            0                            
2     1426.511093    1072.013147  ...            0                            
3     1130.613861    1119.207921  ...            0                            
4     1190.019802    1349.702970  ...            0                            

    ann_truncated  ann_difficult cat_id   cat_name cat_supercategory split  \
id                                                                           
0                                     0  fractured                           
1                                     0  fractured                           
2                                     0  fractured                           
3                                     0  fractured                           
4                                     0  fractured                           

   annotated  
id            
0          1  
1          1  
2          1  
3          1  
4          1  

[5 rows x 26 columns]

In [6]:
dataset.df['img_folder'][0]+'/'+ dataset.df['img_filename'][0]

'/kaggle/input/fracatlas-original-dataset/FracAtlas/images/Fractured/IMG0000019.jpg'

In [7]:
dataset.df[['img_depth', 'ann_segmented', 'ann_bbox_xmin',
       'ann_bbox_ymin', 'ann_bbox_xmax', 'ann_bbox_ymax', 'ann_bbox_width',
       'ann_bbox_height', 'ann_area', 'ann_segmentation']].head()

img_depth ann_segmented  ann_bbox_xmin  ann_bbox_ymin  ann_bbox_xmax  \
id                                                                        
0                             1242.297030     929.108911    1515.564356   
1                             1466.504519    2010.557108    1621.745275   
2                             1426.511093    1072.013147    1570.866064   
3                             1130.613861    1119.207921    1270.811881   
4                             1190.019802    1349.702970    1285.069307   

    ann_bbox_ymax  ann_bbox_width  ann_bbox_height      ann_area  \
id                                                                 
0     1076.435644      273.267327       147.326733  25033.781002   
1     2163.904684      155.240756       153.347576  15220.009428   
2     1187.970419      144.354971       115.957272  13023.273551   
3     1219.009901      140.198020        99.801980   9658.347221   
4     1511.287129       95.049505       161.584158  10558.964807   

                                     ann_segmentation  
id                                                     
0   [[1266.0594059405942, 1045.5445544554457, 1339...  
1   [[1466.504519309778, 2010.557107641742, 1515.7...  
2   [[1554.300739523418, 1076.746096959737, 1457.2...  
3   [[1201.90099009901, 1119.2079207920794, 1130.6...  
4   [[1249.4257425742576, 1349.7029702970299, 1192...

In [8]:
print(f"Number of images: {dataset.analyze.num_images}")
print(f"Number of classes: {dataset.analyze.num_classes}")
print(f"Classes:{dataset.analyze.classes}")
print(f"Class counts:\n{dataset.analyze.class_counts}")
print(f"Path to annotations:\n{dataset.path_to_annotations}")


Number of images: 717
Number of classes: 1
Classes:['fractured']
Class counts:
cat_name
fractured    922
Name: count, dtype: int64
Path to annotations:
/kaggle/input/fracatlas-original-dataset/FracAtlas/Annotations/COCO JSON


In [9]:
# we store this in a variable and make sure to add the non fractured paths to it ! so that the DATAFRAME
# fulfils the purpose. 

df = dataset.df

# I want to create a non fractured df to merge with this !
non_frac_image_folder = '/kaggle/input/fracatlas-original-dataset/FracAtlas/images/Non_fractured'
non_frac_image_filename = glob.glob('/kaggle/input/fracatlas-original-dataset/FracAtlas/images/Non_fractured/*.jpg')




non_frac = pd.DataFrame({'img_folder':non_frac_image_folder, 'img_filename':non_frac_image_filename})

cat_name = 'non fractured' 
non_frac['cat_name'] = cat_name 
non_frac['ann_bbox_xmin'] = 0
non_frac['ann_bbox_ymin'] = 0
non_frac['ann_bbox_xmax'] = 0
non_frac['ann_bbox_ymax'] = 0
non_frac['img_filename'] = non_frac['img_filename'].apply(lambda x: str(x).split('/')[-1])
non_frac.head()

img_folder    img_filename  \
0  /kaggle/input/fracatlas-original-dataset/FracA...  IMG0000650.jpg   
1  /kaggle/input/fracatlas-original-dataset/FracA...  IMG0003236.jpg   
2  /kaggle/input/fracatlas-original-dataset/FracA...  IMG0000869.jpg   
3  /kaggle/input/fracatlas-original-dataset/FracA...  IMG0001904.jpg   
4  /kaggle/input/fracatlas-original-dataset/FracA...  IMG0002241.jpg   

        cat_name  ann_bbox_xmin  ann_bbox_ymin  ann_bbox_xmax  ann_bbox_ymax  
0  non fractured              0              0              0              0  
1  non fractured              0              0              0              0  
2  non fractured              0              0              0              0  
3  non fractured              0              0              0              0  
4  non fractured              0              0              0              0

# Lets Combine

In [10]:
df['img_filename'][0]

'IMG0000019.jpg'

In [11]:
df = pd.concat([df,  non_frac]).sample(frac=1).reset_index(drop = True)

map_class = {'non fractured':0, 'fractured':1}

df['cat_name'] = df['cat_name'].map( map_class )

df.head()

img_folder    img_filename img_path  \
0  /kaggle/input/fracatlas-original-dataset/FracA...  IMG0000956.jpg      NaN   
1  /kaggle/input/fracatlas-original-dataset/FracA...  IMG0002179.jpg      NaN   
2  /kaggle/input/fracatlas-original-dataset/FracA...  IMG0002514.jpg            
3  /kaggle/input/fracatlas-original-dataset/FracA...  IMG0002036.jpg            
4  /kaggle/input/fracatlas-original-dataset/FracA...  IMG0002564.jpg            

   img_id  img_width  img_height img_depth ann_segmented  ann_bbox_xmin  \
0     NaN        NaN         NaN       NaN           NaN       0.000000   
1     NaN        NaN         NaN       NaN           NaN       0.000000   
2   371.0      373.0       454.0                             157.402219   
3   136.0      373.0       454.0                             215.597781   
4   419.0      373.0       454.0                              92.864832   

   ann_bbox_ymin  ...  ann_iscrowd  ann_keypoints  ann_pose  ann_truncated  \
0       0.000000  ...          NaN            NaN       NaN            NaN   
1       0.000000  ...          NaN            NaN       NaN            NaN   
2     240.243221  ...          0.0                                           
3     122.359901  ...          0.0                                           
4     238.004930  ...          0.0                                           

   ann_difficult cat_id  cat_name cat_supercategory split annotated  
0            NaN    NaN         0               NaN   NaN       NaN  
1            NaN    NaN         0               NaN   NaN       NaN  
2                     0         1                               1.0  
3                     0         1                               1.0  
4                     0         1                               1.0  

[5 rows x 26 columns]

In [12]:
df.loc[0,['ann_bbox_xmin',
       'ann_bbox_ymin', 'ann_bbox_xmax', 'ann_bbox_ymax']].values.astype(float)

array([0., 0., 0., 0.])

In [13]:
import os
import pandas as pd
from PIL import Image
import torch
from torch.utils.data import Dataset, DataLoader, SubsetRandomSampler
from torchvision import transforms
import numpy as np

class NormalizeTransform:
    def __call__(self, image):
        image = np.array(image)
        normalized = (image - np.mean(image)) / np.std(image)
        return Image.fromarray((normalized * 255).astype(np.uint8))

class CustomDataset(Dataset):
    def __init__(self, frame, root_dir, transform=None):
        self.data_frame = frame
        self.root_dir = frame['img_folder']
        self.transform = transform

    def __len__(self):
        return len(self.data_frame)

    def __getitem__(self, idx):
        img_name = os.path.join(str(self.root_dir[idx]), str(self.data_frame['img_filename'][idx]))
        image = Image.open(img_name).convert('RGB')
        label = int(self.data_frame['cat_name'][idx])
        if label == 1:  # Assuming '1' corresponds to 'fractured'
            bbox = self.data_frame.loc[idx, ['ann_bbox_xmin', 'ann_bbox_ymin', 'ann_bbox_xmax', 'ann_bbox_ymax']].values.astype('float')
        else:
            bbox = np.array([0.0, 0.0, 0.0, 0.0])  # Default bounding box for 'not fractured'
        
        if self.transform:
            image = self.transform(image)

        return image, label, torch.from_numpy(bbox)

# Define transformations
transform = transforms.Compose([
    transforms.Resize((224, 224)),
    transforms.ToTensor(),
#     NormalizeTransform(),
    transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225]),
])

# Create dataset and DataLoader
frame = df
root_dir = '/kaggle/input/fracatlas-original-dataset/FracAtlas/images'
dataset = CustomDataset(frame=frame, root_dir=root_dir, transform=transform)

batch_size = 16
validation_split = 0.2
shuffle_dataset = True
random_seed = 42

# Creating data indices for training and validation splits
dataset_size = len(dataset)
indices = list(range(dataset_size))
split = int(np.floor(validation_split * dataset_size))

if shuffle_dataset:
    np.random.seed(random_seed)
    np.random.shuffle(indices)

train_indices, val_indices = indices[split:], indices[:split]

# Creating PT data samplers and loaders
train_sampler = SubsetRandomSampler(train_indices)
valid_sampler = SubsetRandomSampler(val_indices)

train_loader = DataLoader(dataset, batch_size=batch_size, sampler=train_sampler)
validation_loader = DataLoader(dataset, batch_size=batch_size, sampler=valid_sampler)

# Verify the DataLoaders
print(f"Number of training samples: {len(train_indices)}")
print(f"Number of validation samples: {len(val_indices)}")


Number of training samples: 3431
Number of validation samples: 857


In [14]:
gc.collect()
torch.cuda.empty_cache()


In [15]:
import torch
import torch.nn as nn
import torchvision.models as models

device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")

class MultiHeadAttentionMobileNetV2(nn.Module):
    def __init__(self, num_classes, num_heads=8):
        super(MultiHeadAttentionMobileNetV2, self).__init__()
        self.mobilenet = models.mobilenet_v2(pretrained=True).to(device)
        self.mobilenet_features = nn.Sequential(*list(self.mobilenet.features.children()))
        # Adjust d_model according to the output shape of the mobilenet_features
        d_model = 1280  # Final layer output dimension of MobileNetV2
        
        # Flatten layer
        self.flatten = nn.Flatten()
        
        # Multi-Head Attention
        self.attention = nn.MultiheadAttention(embed_dim=d_model, num_heads=num_heads)
        
        # Bounding box regression head
        self.bboxHead = nn.Sequential(
            nn.Linear(d_model, 512),
            nn.ReLU(),
            nn.Linear(512, 128),
            nn.ReLU(),
            nn.Linear(128, 64),
            nn.ReLU(),
            nn.Linear(64, 32),
            nn.ReLU(),
            nn.Linear(32, 4),
            nn.Sigmoid()
        )
        
        # Classification head
        self.softmaxHead = nn.Sequential(
            nn.Linear(d_model, 512),
            nn.ReLU(),
            nn.Dropout(0.5),
            nn.Linear(512, 512),
            nn.ReLU(),
            nn.Dropout(0.5),
            nn.Linear(512, num_classes),
            nn.Softmax(dim=1)
        )
        
    def forward(self, x):
        x = self.mobilenet_features(x)
        
        x = x.mean([2, 3])  # Global average pooling
        
        # Multi-Head Attention requires (L, N, E) shape
        x = x.unsqueeze(0)
        attn_output, _ = self.attention(x, x, x)
        attn_output = attn_output.squeeze(0)
        
        bbox_output = self.bboxHead(attn_output)
        class_output = self.softmaxHead(attn_output)
        
        return bbox_output, class_output

# Assuming you have `num_classes` defined as the number of classes in your dataset
num_classes = 2  # replace with your actual number of classes
model = MultiHeadAttentionMobileNetV2(num_classes=num_classes).to(device)

# Print the model architecture
print(model)


/opt/conda/lib/python3.10/site-packages/torchvision/models/_utils.py:208: UserWarning: The parameter 'pretrained' is deprecated since 0.13 and may be removed in the future, please use 'weights' instead.
  warnings.warn(
/opt/conda/lib/python3.10/site-packages/torchvision/models/_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=MobileNet_V2_Weights.IMAGENET1K_V1`. You can also use `weights=MobileNet_V2_Weights.DEFAULT` to get the most up-to-date weights.
  warnings.warn(msg)
Downloading: "https://download.pytorch.org/models/mobilenet_v2-b0353104.pth" to /root/.cache/torch/hub/checkpoints/mobilenet_v2-b0353104.pth
100%|██████████| 13.6M/13.6M [00:00<00:00, 109MB/s] 


MultiHeadAttentionMobileNetV2(
  (mobilenet): MobileNetV2(
    (features): Sequential(
      (0): Conv2dNormActivation(
        (0): Conv2d(3, 32, kernel_size=(3, 3), stride=(2, 2), padding=(1, 1), bias=False)
        (1): BatchNorm2d(32, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
        (2): ReLU6(inplace=True)
      )
      (1): InvertedResidual(
        (conv): Sequential(
          (0): Conv2dNormActivation(
            (0): Conv2d(32, 32, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), groups=32, bias=False)
            (1): BatchNorm2d(32, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
            (2): ReLU6(inplace=True)
          )
          (1): Conv2d(32, 16, kernel_size=(1, 1), stride=(1, 1), bias=False)
          (2): BatchNorm2d(16, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
        )
      )
      (2): InvertedResidual(
        (conv): Sequential(
          (0): Conv2dNormActivation(
            (0): Conv2d(16

In [16]:
import torch.optim as optim
from sklearn.model_selection import StratifiedKFold
from tqdm import tqdm
# Assuming you have `num_classes` defined as the number of classes in your dataset
num_classes = 2  # replace `lb.classes_` with your actual label classes

# Initialize the model, loss functions, and optimizer
criterion_class = nn.CrossEntropyLoss()
criterion_bbox = nn.MSELoss()
optimizer = optim.Adam(model.parameters(), lr=1e-4)
scheduler = optim.lr_scheduler.CosineAnnealingWarmRestarts(optimizer, T_0=10)

# WandB configuration
wandb.watch(model, log="all")
num_epochs = 70
# K-Fold Cross Validation
kf = StratifiedKFold(n_splits=5)
best_val_loss = float('inf')

for fold, (train_idx, val_idx) in enumerate(kf.split(np.zeros(len(frame)), frame['cat_name'])):
    print(f'Fold {fold + 1}')
    
    # Creating PT data samplers and loaders
    train_sampler = SubsetRandomSampler(train_idx)
    valid_sampler = SubsetRandomSampler(val_idx)
    gc.collect()
    torch.cuda.empty_cache()

    train_loader = DataLoader(dataset, batch_size=batch_size, sampler=train_sampler)
    validation_loader = DataLoader(dataset, batch_size=batch_size, sampler=valid_sampler)
    
    for epoch in tqdm(range(num_epochs),desc='epochs'):
        model.train()
        running_loss = 0.0
        for images, labels, bboxes in tqdm(train_loader,desc='loader train'):
            images = images.to(device).float()
            labels = labels.to(device).long()
            bboxes = bboxes.to(device).float()
#             print(images[:-1])
            optimizer.zero_grad()

            # Forward pass
            bbox_output, class_output = model(images)

            # Compute the classification loss
            loss_class = criterion_class(class_output, labels)

            # Compute the bounding box loss only for 'fractured' images
            fractured_mask = labels == 1
            if fractured_mask.any():
                loss_bbox = criterion_bbox(bbox_output[fractured_mask], bboxes[fractured_mask])
                loss_bbox = loss_bbox.float()  # Ensure loss_bbox is float32
            else:
                loss_bbox = torch.tensor(0.0, device=device).float()  # Handle case where no fractured images are in batch

            # Combine the losses
            loss = loss_class + loss_bbox

            # Ensure the combined loss is float32
            loss = loss.float()

            # Backward pass and optimization
            loss.backward()
            optimizer.step()

            running_loss += loss.item()

            # Log training metrics to wandb
            wandb.log({"train_loss": loss.item()})

        # Validation phase
        model.eval()
        val_running_loss = 0.0
        with torch.no_grad():
            for images, labels, bboxes in tqdm(validation_loader,desc='val loader'):
                images = images.to(device).float()
                labels = labels.to(device).long()
                bboxes = bboxes.to(device).float()

                # Forward pass
                bbox_output, class_output = model(images)

                # Compute the classification loss
                loss_class = criterion_class(class_output, labels)

                # Compute the bounding box loss only for 'fractured' images
                fractured_mask = labels == 1
                if fractured_mask.any():
                    loss_bbox = criterion_bbox(bbox_output[fractured_mask], bboxes[fractured_mask])
                    loss_bbox = loss_bbox.float()
                else:
                    loss_bbox = torch.tensor(0.0, device=device).float()

                # Combine the losses
                loss = loss_class + loss_bbox
                loss = loss.float()

                val_running_loss += loss.item()

        avg_train_loss = running_loss / len(train_loader)
        avg_val_loss = val_running_loss / len(validation_loader)

        print(f'Epoch [{epoch + 1}/{num_epochs}], Train Loss: {avg_train_loss}, Val Loss: {avg_val_loss}')

        # Log validation metrics to wandb
        wandb.log({"val_loss": avg_val_loss})

        # Save the model if the validation loss is the best we've seen so far
        if avg_val_loss < best_val_loss:
            best_val_loss = avg_val_loss
            torch.save(model.state_dict(), 'best_model.pth')
            print(f'Model saved at epoch {epoch + 1} with validation loss: {avg_val_loss}')

        # Step the scheduler
        scheduler.step()

print('Training completed.')

Fold 1


loader train: 100%|██████████| 215/215 [01:26<00:00,  2.48it/s]

epochs:   1%|▏         | 1/70 [01:43<1:59:31, 103.93s/it]

Epoch [1/70], Train Loss: 266755.6459019808, Val Loss: 263403.7693865741
Model saved at epoch 1 with validation loss: 263403.7693865741



loader train: 100%|██████████| 215/215 [00:54<00:00,  3.98it/s]

epochs:   3%|▎         | 2/70 [02:48<1:31:18, 80.57s/it] 

Epoch [2/70], Train Loss: 287837.1016240924, Val Loss: 255255.4070880402
Model saved at epoch 2 with validation loss: 255255.4070880402


...

Epoch [68/70], Train Loss: 234725.38334375288, Val Loss: 349434.12941261573



loader train: 100%|██████████| 215/215 [00:55<00:00,  3.87it/s]

epochs:  99%|█████████▊| 69/70 [1:17:01<01:07, 67.08s/it]

Epoch [69/70], Train Loss: 257156.45119413358, Val Loss: 402678.69201316766



loader train: 100%|██████████| 215/215 [00:53<00:00,  4.01it/s]

epochs: 100%|██████████| 70/70 [1:18:07<00:00, 66.96s/it]

Epoch [70/70], Train Loss: 227838.62431268388, Val Loss: 402351.67386429396
Training completed.


In [17]:
wandb.finish()

wandb:                                                                                
wandb: 
wandb: Run history:
wandb: train_loss ▁▁▅▁█▂▁▃▇▄▄▁▁▁▁▃▄▃▁▁▁▁▃▂▇▁▁▁▁▁▄▁▁▁▁▄▅▄▂▆
wandb:   val_loss ▃▃▃▃▄▃▄▄▁▁▃▁▂▂▃▂▃▂▃▂▃▃▂▂▂▃▃▃▃▃▃▂▅▅█▅▆▆▆▅
wandb: 
wandb: Run summary:
wandb: train_loss 0.31326
wandb:   val_loss 402351.67386
wandb: 
wandb: 🚀 View run fearless-lion-10 at: https://wandb.ai/shyam-d-gupta/fracatlas-fracture-bbox-labels-effnet-k-fold/runs/lnzvqbpk
wandb: ⭐️ View project at: https://wandb.ai/shyam-d-gupta/fracatlas-fracture-bbox-labels-effnet-k-fold
wandb: Synced 5 W&B file(s), 0 media file(s), 0 artifact file(s) and 0 other file(s)
wandb: Find logs at: ./wandb/run-20240613_124939-lnzvqbpk/logs
